# Inhaltsbasiertes Empfehlungssystem mit KNN-Klassifikation

## Schritt 1: Einschränken der Daten und Festlegen des Nutzers

Zunächst müssen wir den Datensatz auf eine Auswahl von Filmen einschränken, da die Berechnungen sonst zu lange dauern würden. Außerdem kannst du festlegen, für welchen Nutzer du Empfehlungen berechnen möchtest.

In [1]:
nutzer = 2
schranke = 1000

## Schritt 2: Datensatzvorbereitung 

Wie genau der Datensatz vorbereitet wird findest du in Kapitel 14.5.1.2.

<i>Falls du eine Warnmeldung erhälst, kannst du diese ignorieren.</i>

In [2]:
import pandas as pd
import re

ratings = pd.read_csv(r'ratings.csv',encoding='latin-1')
movies = pd.read_csv(r'movies.csv',encoding='latin-1')

movies_filter = movies[movies['movieId']<schranke]
for elem in movies_filter['genres'].str.split(pat = '|', expand = False).explode().unique():
    column = []
    for i in range(len(movies_filter)):
        if elem in movies_filter['genres'].str.split(pat = '|', expand = False)[i]:
            column.append(1)
        else:
            column.append(0)
    movies_filter[elem] = column
movies_filter = movies_filter.drop(['title','genres'], axis='columns')

ratings_user = ratings[ratings['userId']==nutzer]
total_user = pd.merge(movies_filter,ratings_user,left_on=['movieId'],
              right_on=['movieId'],
              how='inner').drop(['userId','timestamp'], axis='columns')
total_user

<ipython-input-2-cc95fcc5d215>:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movies_filter[elem] = column


movieId  Adventure  Animation  Children  Comedy  Fantasy  Romance  Drama  \
0         1          1          1         1       1        1        0      0   
1        62          0          0         0       0        0        0      1   
2       110          0          0         0       0        0        0      1   
3       150          1          0         0       0        0        0      1   
4       151          0          0         0       0        0        1      1   
5       236          0          0         0       1        0        1      0   
6       260          1          0         0       0        0        0      0   
7       261          0          0         0       0        0        0      1   
8       266          0          0         0       0        0        1      1   
9       318          0          0         0       0        0        0      1   
10      333          0          0         0       1        0        0      0   
11      349          0          0         0       0        0        0      1   
12      356          0          0         0       1        0        1      1   
13      364          1          1         1       0        0        0      1   
14      380          1          0         0       1        0        1      0   
15      457          0          0         0       0        0        0      0   
16      480          1          0         0       0        0        0      0   
17      497          0          0         0       1        0        1      0   
18      524          0          0         0       0        0        0      1   
19      527          0          0         0       0        0        0      1   
20      534          0          0         0       0        0        1      1   
21      553          0          0         0       0        0        0      1   
22      588          1          1         1       1        0        0      0   
23      589          0          0         0       0        0        0      0   
24      653          1          0         0       0        1        0      0   
25      733          1          0         0       0        0        0      0   
26      858          0          0         0       0        0        0      1   
27      914          0          0         0       1        0        1      1   
28      953          0          0         1       0        1        1      1   

    Action  Crime  ...  Horror  Mystery  Sci-Fi  IMAX  Documentary  War  \
0        0      0  ...       0        0       0     0            0    0   
1        0      0  ...       0        0       0     0            0    0   
2        1      0  ...       0        0       0     0            0    1   
3        0      0  ...       0        0       0     1            0    0   
4        1      0  ...       0        0       0     0            0    1   
5        1      0  ...       0        0       0     0            0    0   
6        1      0  ...       0        0       1     0            0    0   
7        0      0  ...       0        0       0     0            0    0   
8        0      0  ...       0        0       0     0            0    1   
9        0      1  ...       0        0       0     0            0    0   
10       0      0  ...       0        0       0     0            0    0   
11       1      1  ...       0        0       0     0            0    0   
12       0      0  ...       0        0       0     0            0    1   
13       0      0  ...       0        0       0     1            0    0   
14       1      0  ...       0        0       0     0            0    0   
15       0      0  ...       0        0       0     0            0    0   
16       1      0  ...       0        0       1     0            0    0   
17       0      0  ...       0        0       0     0            0    0   
18       0      0  ...       0        0       0     0            0    0   
19       0      0  ...       0        0       0     0            0    1   
20       0      0  ...      

## Schritt 3: Klassen und Attribute angeben

Um unser Modell zu trainieren, müssen wir dem Modell sagen, welches die Attribute und welches die Klassen sind, die es vorhersagen soll. Dafür trennen wir den DataFrame in die Attribute, d.h. alle Genre Spalten, und die Klasse, die Spalte ratings.

In [4]:
X = total_user.drop(['rating','movieId'], axis='columns')
y = total_user.rating
X

Adventure  Animation  Children  Comedy  Fantasy  Romance  Drama  Action  \
0           1          1         1       1        1        0      0       0   
1           0          0         0       0        0        0      1       0   
2           0          0         0       0        0        0      1       1   
3           1          0         0       0        0        0      1       0   
4           0          0         0       0        0        1      1       1   
5           0          0         0       1        0        1      0       1   
6           1          0         0       0        0        0      0       1   
7           0          0         0       0        0        0      1       0   
8           0          0         0       0        0        1      1       0   
9           0          0         0       0        0        0      1       0   
10          0          0         0       1        0        0      0       0   
11          0          0         0       0        0        0      1       1   
12          0          0         0       1        0        1      1       0   
13          1          1         1       0        0        0      1       0   
14          1          0         0       1        0        1      0       1   
15          0          0         0       0        0        0      0       0   
16          1          0         0       0        0        0      0       1   
17          0          0         0       1        0        1      0       0   
18          0          0         0       0        0        0      1       0   
19          0          0         0       0        0        0      1       0   
20          0          0         0       0        0        1      1       0   
21          0          0         0       0        0        0      1       1   
22          1          1         1       1        0        0      0       0   
23          0          0         0       0        0        0      0       1   
24          1          0         0       0        1        0      0       1   
25          1          0         0       0        0        0      0       1   
26          0          0         0       0        0        0      1       0   
27          0          0         0       1        0        1      1       0   
28          0          0         1       0        1        1      1       0   

    Crime  Thriller  Horror  Mystery  Sci-Fi  IMAX  Documentary  War  Musical  \
0       0         0       0        0       0     0            0    0        0   
1       0         0       0        0       0     0            0    0        0   
2       0         0       0        0       0     0            0    1        0   
3       0         0       0        0       0     1            0    0        0   
4       0         0       0        0       0     0            0    1        0   
5       0         0       0        0       0     0            0    0        0   
6       0         0       0        0       1     0            0    0        0   
7       0         0       0        0       0     0            0    0        0   
8       0         0       0        0       0     0            0    1        0   
9       1         0       0        0       0     0            0    0        0   
10      0         0       0        0       0     0            0    0        0   
11      1         1       0        0       0     0            0    0        0   
12      0         0       0        0       0     0            0    1        0   
13      0         0       0        0       0     1            0    0        1   
14      0         1       0        0       0     0            0    0        0   
15      0         1       0        0       0     0            0    0        0   
16      0         1       0        0       1     0            0    0        0   
17      0         0       0        0       0     0            0    0        0   
18      0         0       0        0       0     0            0    0        0   
19      0    

## Schritt 4: Diskretisieren

Wenn du dir die Spalte 'ratings' anzeigen lässt, siehst du, dass sie Bewertungen mit halben Sternen, d.h. 3.5 oder 4.5 enthält. Die Funktion der KNN-Klassifikation von python kann nur mit ganzzahligen Klassen arbeiten. Daher müssen wir Einträge der Spalte 'ratings' ganzzahligen Werten zuordnen. Wir können entweder runden, oder eine python-Funktion verwenden, die automatisch ganzzahlige Klassen zuordnet. Im zweiten Fall müssen wir die Vorhersagen wieder zurück interpretieren, also aus den ganzzahligen Klassen wieder die Bewertungen auslesen. Führe die Variante aus, die du nutzen möchtest.

### Achtung: Führe nur eine der beiden Varianten aus!

### Variante Runden

In [ ]:
y_ganzzahlig = y.astype(int)

### Variante python Funktion

In [5]:
from sklearn import preprocessing
from sklearn import utils

lab = preprocessing.LabelEncoder()
y_transformed = lab.fit_transform(y)
print(y_transformed)
print(y.to_list())

[4 0 7 5 6 5 7 0 1 7 7 6 6 6 1 7 2 5 4 7 6 2 2 5 3 6 4 5 6]
[3.5, 0.5, 5.0, 4.0, 4.5, 4.0, 5.0, 0.5, 1.0, 5.0, 5.0, 4.5, 4.5, 4.5, 1.0, 5.0, 2.0, 4.0, 3.5, 5.0, 4.5, 2.0, 2.0, 4.0, 3.0, 4.5, 3.5, 4.0, 4.5]


## Schritt 5: Modell trainieren

Nun trainieren wir das Modell auf unserem Datensatz. Du kannst angeben, wie viele nächste Nachbarn das Modell berücksichtigen soll. Wenn das Modell trainiert ist erhälst du die Ausgabe 'KNeighborsClassifier(n_neighbors=3)'.

In [9]:
nachbarn_anzahl = 3

from sklearn.neighbors import KNeighborsClassifier
knn = KNeighborsClassifier(n_neighbors=nachbarn_anzahl)
knn.fit(X, y_transformed)

KNeighborsClassifier(n_neighbors=3)

### Schritt 6: Filmempfehlungssystem verwenden!

Wir nutzen das Empfehlungssystem, um Bewertungen für einen neuen Film zu prognostizieren.<br/>
Suche dafür einen Film aus und bestimme die Attribute dieses Films. Erstelle dazu eine Liste mit den Genrezugehörigkeiten. Hier ist ein Beispiel für einen Film gegeben, der den Genres Comedy, Romance und Musical zugeordnet wird. Die Liste aller Attribute lautet für unseren Datensatz [Adventure, Animation, Children, Comedy, Fantasy, Romance, Drama, Action, Crime, Thriller, Horror, Mystery, Sci-Fi, IMAX, Documentary, War, Musical, Western, Film-Noir]. 

In [6]:
neuer_film = {"Adventure":[0], "Animation":[0],"Children":[0],"Comedy":[1],"Fantasy":[0],"Romance":[1],"Drama":[0],"Action":[0],"Crime":[0],"Thriller":[0],"Horror":[0],"Mystery":[0],"Sci-Fi":[0],"IMAX":[0],"Documentary":[0],"War":[0],"Muscial":[1],"Western":[0], "Film-Noir":[0]}

In [7]:
film = pd.DataFrame(neuer_film)
film

Adventure  Animation  Children  Comedy  Fantasy  Romance  Drama  Action  \
0          0          0         0       1        0        1      0       0   

   Crime  Thriller  Horror  Mystery  Sci-Fi  IMAX  Documentary  War  Muscial  \
0      0         0       0        0       0     0            0    0        1   

   Western  Film-Noir  
0        0          0

Hier wird eine Bewertung vorhergesagt. Führe die zweite Codezelle nur aus, wenn du die Version python Funktion gewählt hast, um die Vorhersage wieder zu decodieren, also als Bewertung ausgeben zu lassen.

In [10]:
knn.predict(film)

array([5], dtype=int64)

In [11]:
lab.inverse_transform(knn.predict(film))

array([4.])